# Lab 19 - k-nearest neighbors

The *k-nearest neighbors* algorithm predicts based on the values of the k closest training data.  For example, a 3-nearest neighbor algorithm will find the 3 closest data points (using the Euclidean distance) in the training data and use them to make a prediction.

If we are classifying (trying to predict qualitative value), the prediction is the class that appears the most in the k neighbors.

If we are performing regression (trying to predict a quantitative value), the prediction is the mean of the y values of the k neighbors.

## Classifier

We will return to the city services survey data from Lab 12 (Decision tree classifiers).  Recall that this data is collected by the city of [Somerville, MA](https://en.wikipedia.org/wiki/Somerville,_Massachusetts) asking residents about their happiness, as well as ratings of city services. 

The link to download the data is [https://archive.ics.uci.edu/ml/machine-learning-databases/00479/SomervilleHappinessSurvey2015.csv](https://archive.ics.uci.edu/ml/machine-learning-databases/00479/SomervilleHappinessSurvey2015.csv)

The data columns are:

- D = decision attribute (D) with values 0 (unhappy) and 1 (happy) 
- X1 = the availability of information about the city services 
- X2 = the cost of housing 
- X3 = the overall quality of public schools 
- X4 = your trust in the local police 
- X5 = the maintenance of streets and sidewalks 
- X6 = the availability of social community events 

Attributes X1 to X6 have values 1 to 5.

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
 
from sklearn.preprocessing import MinMaxScaler
    
from sklearn.model_selection import train_test_split

from sklearn.neighbors import KNeighborsClassifier
from sklearn.neighbors import KNeighborsRegressor

from sklearn.metrics import confusion_matrix

%matplotlib inline

As in Lab 12, we will read the data into the dataframe `city`, giving the columns more descriptive names in the process.

In [ ]:
new_column_names = ["happy","city_info","housing_cost", "school_quality", \
                    "trust_police", "streets_sidewalks", "community_events"]
city = pd.read_csv("../data/SomervilleHappinessSurvey2015.csv", \
                    encoding = "utf-16le",names = new_column_names, \
                    header = 0)
city.head()

Define a variable `X` to contain all columns except `happy`.

<details> <summary>Answer:</summary>
<code>X = city.iloc[:,1:7]</code>
</details>

Define a variable y to be the `happy` column.

<details> <summary>Answer:</summary>
<code>y =city["happy"]</code>
</details>

Split your X and y data into training and testing data.

<details> <summary>Answer:</summary>
<code>X_train, X_test, y_train, y_test = train_test_split(X,y, test_size = 0.2)</code>
</details>

The following code creates a 3-nearest neighbor classifier (k = 3), fits the training data to it, and makes predictions for the test data. 

In [ ]:
k3nn = KNeighborsClassifier(n_neighbors = 3)
k3nn.fit(X_train, y_train)
y_pred = k3nn.predict(X_test)

Compute a confusion matrix for the true values and predictions.

<details> <summary>Answer:</summary>
<code>confusion_matrix(y_test, y_pred, labels = [1,0])</code>
</details>

Compute the sensitivity, specificity, precision, and accuracy from the confusion matrix.

<details> <summary>Answer:</summary>
<code>tn, fn, fp, tp = confusion_matrix(y_test, y_pred, labels = [1,0]).ravel()

sensitivity = tp/(tp + fn)
specificity = tn/(tn + fp)
precision = tp/(tp + fp)
accuracy = (tp + tn)/(tp + tn + fp + fn)

print("Sensitivity:",sensitivity)
print("Specificity:",specificity)
print("Precision:", precision)
print("Accuracy:",accuracy)</code>
</details>

How does changing k, the number of neighbors used to make the prediction, affect the performance of this classifier?

The results from the decision tree in Lab 12 were: 

Sensitivity: 0.5584415584415584

Specificity: 0.8181818181818182

Precision: 0.7818181818181819

Accuracy: 0.6783216783216783

How does the k-nearest neighbor classifier compare to the decision tree classifier?

## Regressor

To test k-nearest neighbors for regression, we will use the insurance data from Labs 7, 8, and 13.  Recall we are trying to predict the insurance cost, a quantitative value.  

If you don't have the dataset, download it from GitHub: [https://github.com/stedy/Machine-Learning-with-R-datasets/blob/master/insurance.csv](https://github.com/stedy/Machine-Learning-with-R-datasets/blob/master/insurance.csv)

In this data, each row represents an insurance policy and the 7 columns contain the following information about it:
- age: age of policy holder
- sex: sex of policy holder
- bmi: boday mass index (bmi) of policy holder.  bmi is a (sometimes unreliable) measurement of body fat in adults
- children: number of children (dependents) on the policy
- smoker: whether the policy holder is a smoker
- region: region of the country the policy holder lives in
- charges: price for insurance policy

Read in the insurance data, replacing the qualitative columns with dummy variables.

Create an X variable with the independent variable columns (everything except the charges column).

Create a y variable with the `charges` column.

Split your X and y data into training and testing data.

The following code creates a 3-nearest neighbor regressor (k = 3), fits the training data to it, and makes predictions for the test data.

In [ ]:
ik3nn = KNeighborsRegressor(n_neighbors = 3)
ik3nn.fit(iX_train, iy_train)
iy_pred = ik3nn.predict(iX_test)

Compute the mean squared error for your predictions.

### Scaling data (aka normalization)

When the columns have different scales, the largest column will dominate.  We can get better results by scaling all of our columns to be between 0 and 1.  The scaling formula is:

$$x_{scaled} = \frac{x - x_{\min}}{x_{\max} - x_{\min}}$$

We can use a built in function in sci-kit learn to do the scaling:

In [ ]:
scaler = MinMaxScaler(feature_range=(0, 1))

In [ ]:
iX_train_scaled = scaler.fit_transform(iX_train)
iX_train_scaled

Scale your X test data.  We do not need to scale the y data.

Built a 3-nearest neighbor regressor with the scaled training data and use it to make predictions for the scaled test data.

Compute the new mean squared error.  Does scaling improve the 3-nearest neighbor regressor?

To figure out which value of k to use, we can write a loop to try all values of k between 1 and 20, and compute the mean squared error for each one.  The pseudo-code to do this is:

<code>
create an empty list
loop k from 1 to 20:
    create a k-nearest neighbor regressor
    fit the training data to the k-nearest neighbor regressor
    make predictions for the test data
    compute the mean squared error for the predictions
    store the mean squared error in the list
</code>

In [ ]:
mses = []
for k in range(1,21):
    iknn_scaled = KNeighborsRegressor(n_neighbors = k)
    iknn_scaled.fit(iX_train_scaled, iy_train)
    iy_pred_scaled = iknn_scaled.predict(iX_test_scaled)
    mse = ((iy_pred_scaled - iy_test)**2).mean()
    mses.append(mse)

<details> <summary>Answer:</summary>
<code>
mses = []
for k in range(1,21):
    iknn_scaled = KNeighborsRegressor(n_neighbors = k)
    iknn_scaled.fit(iX_train_scaled, iy_train)
    iy_pred_scaled = iknn_scaled.predict(iX_test_scaled)
    mse = ((iy_pred_scaled - iy_test)**2).mean()
    mses.append(mse)
</code>
</details>

Plot the list of mean squared errors.  The lowest one will correspond to the best k.

Just as with linear regression, we can see if there is a pattern to which values are predicted correctly and which are not.  Plot a scatter plot with the true y test values on the x axis, and the predicted value - the true value on the y axis.